In [13]:
## 计算subsystem 1   keras resnet
import tensorflow as tf
from tensorflow.keras.layers import Dense
from tensorflow.keras import Model
from tensorflow.keras.backend import clear_session
import numpy as np
from matplotlib import pyplot as plt
import os
import tensorflow_probability as tfp
import scipy.io as scio

dataFile = "xdata"  
data = scio.loadmat(dataFile)
xdata = data['xdata']

dataFile = "ydata"  
data = scio.loadmat(dataFile)
ydata = data['ydata']

dataFile = "zdata"  
data = scio.loadmat(dataFile)
zdata = data['zdata']

dataFile = "wdata"  
data = scio.loadmat(dataFile)
wdata = data['wdata']

dataFile = "Ldata"  
data = scio.loadmat(dataFile)
Ldata = data['Ldata']

dataFile = "iptdata"  
data = scio.loadmat(dataFile)
iptdata = data['iptdata']
#ydata=tf.reshape(ydata, [Nu, 1])

Nu=xdata.shape[1]
xdata=tf.reshape(xdata, [Nu])
ydata=tf.reshape(ydata, [Nu])
zdata=tf.reshape(zdata, [Nu])
wdata=tf.reshape(wdata, [Nu])

ipt=tf.cast(iptdata, dtype=tf.int32)
ipt =tf.reduce_sum(ipt, axis=0)
L=tf.cast(Ldata, dtype=tf.int32)
L=tf.reduce_sum(L, axis=0)
iptnp=ipt.numpy()
print(iptnp)
L=L.numpy()
LS=800
Ls=2

I01=tf.argmax(L)
print(I01, iptnp[I01])
i=I01
u1_train =xdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])]
u2_train =ydata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])]
u3_train =zdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])]
u4_train =wdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])]
v1_train =xdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)]
v2_train =ydata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)]
v3_train =zdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)]
v4_train =wdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)]
print(u1_train,u2_train,u3_train,u4_train)
u_train=tf.stack([u1_train,u2_train,u3_train,u4_train],axis=1)
v_train=tf.stack([v1_train,v2_train,v3_train,v4_train],axis=1)
u_train=tf.cast(u_train, dtype=tf.float32)
v_train=tf.cast(v_train, dtype=tf.float32)
print(u_train)
print(v_train)

class myModel(Model):
  def __init__(self):
    super(myModel,self).__init__()
    self.layer1=Dense(20, activation='relu')
    self.layer2=Dense(20, activation='relu')
    self.layer3=Dense(20, activation='relu')
    self.layer4=Dense(20, activation='relu')
    self.layer5=Dense(20, activation='relu')
    self.layer6=Dense(20, activation='relu')
    self.layer7=Dense(20, activation='relu')
    self.layer8=Dense(20, activation='relu')
    self.layer9=Dense(4, kernel_regularizer=tf.keras.regularizers.l2())
  
  def call(self, x):
    x1=self.layer1(x)
    x1=self.layer2(x1)
    x1=self.layer3(x1)
    x1=self.layer4(x1)
    x1=self.layer5(x1)
    x1=self.layer6(x1)
    x1=self.layer7(x1)
    x1=self.layer8(x1)
    y=self.layer9(x1)
    y=y+x
    return y

model1=myModel()

model1.compile(optimizer='adam', loss='mse')

model1.fit(u_train, v_train, batch_size=128, epochs=2000, validation_split=0.01, validation_freq=20)

model1.summary()


[  0 209 798   0 184 798   0 162 798   0 146 798   0 141 798   0 132 798
   0 129 798   0 123 798   0 120 798   0 119 798   0 186 798   0 163 798
   0 147 798   0 139 798   0 131 798   0 126 798   0 122 798   0 119 798
   0 114 798   0 111 798   0 168 798   0 154 798   0 142 798   0 131 798
   0 121 798   0 116 798   0 112 798   0 109 798   0 110 798   0 104 798
   0 160 798   0 144 798   0 131 798   0 118 798   0 117 798   0 111 798
   0 105 798   0 100 798   0 100 798   0 100 798   0 153 798   0 140 798
   0 122 798   0 116 798   0 111 798   0 105 798   0 100 798   0 100 798
   0  94 798   0  93 798   0 141 798   0 128 798   0 116 798   0 109 798
   0 105 798   0  99 798   0  96 798   0  91 798   0  90 798   0  87 798
   0 137 798   0 122 798   0 115 798   0 103 798   0  96 798   0  91 798
   0  91 798   0  86 798   0  83 798   0  83 798   0 130 798   0 115 798
   0 105 798   0  97 798   0  94 798   0  87 798   0  86 798   0  80 798
   0  79 798   0  78 798   0 124 798   0 111 798   

In [21]:
## 计算其他几段数据误差
LI0=0
for k in range(2):
    print(k,'---------------------------------------')
    Llen=L.size
    error=np.zeros([Llen])
    for i in range(Llen):
        x1=tf.cast(xdata[LS*(i//Ls)+iptnp[i+i//Ls]], dtype=tf.float32)
        x1=tf.reshape(x1,[1])
        x2=tf.cast(ydata[LS*(i//Ls)+iptnp[i+i//Ls]],dtype=tf.float32)
        x2=tf.reshape(x2,[1])
        x3=tf.cast(zdata[LS*(i//Ls)+iptnp[i+i//Ls]],dtype=tf.float32)
        x3=tf.reshape(x3,[1])
        x4=tf.cast(wdata[LS*(i//Ls)+iptnp[i+i//Ls]],dtype=tf.float32)
        x4=tf.reshape(x4,[1])
        u=tf.stack([x1,x2,x3,x4],axis=1)
        y1=np.zeros([4,L[i]])
        u1=tf.reduce_sum(u,axis=0)
        y1[:,0]=u1.numpy()
        for j in range(L[i]-1):
            clear_session()
            v=model1.predict(u, verbose=0)
            v=tf.constant(v)
            u=v
            y1[:,j+1]=v.numpy()
        
        y1=tf.cast(y1, dtype=tf.float32)
        ytrue1=tf.cast(xdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])], dtype=tf.float32)
        ytrue2=tf.cast(ydata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])], dtype=tf.float32)
        ytrue3=tf.cast(zdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])], dtype=tf.float32)
        ytrue4=tf.cast(wdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])], dtype=tf.float32)
        ytrue=tf.stack([ytrue1,ytrue2,ytrue3,ytrue4],axis=0)
        y=(y1-ytrue).numpy()
        #print(i,y1,ytrue)
        error[i]=tf.reduce_mean(np.power(y[0,:],2)+np.power(y[1,:],2)+np.power(y[2,:],2)+np.power(y[3,:],2),axis=0)
        print(i,error[i])
    
    print(error)
    
    
    I=np.where(error<1e-1)[0]
    LI=I.size
    print(I)
    if LI==LI0:
        break
    LI0=LI
    
    u1_train =np.zeros([0])
    u2_train =np.zeros([0])
    u3_train =np.zeros([0])
    u4_train =np.zeros([0])
    v1_train =np.zeros([0])
    v2_train =np.zeros([0])
    v3_train =np.zeros([0])
    v4_train =np.zeros([0])
    for i in I:
        u1_train=np.append(u1_train, xdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])])
        u2_train=np.append(u2_train, ydata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])])
        u3_train=np.append(u3_train, zdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])])
        u4_train=np.append(u4_train, wdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])])
        v1_train=np.append(v1_train, xdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)])
        v2_train=np.append(v2_train, ydata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)])
        v3_train=np.append(v3_train, zdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)])
        v4_train=np.append(v4_train, wdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)])
    
    u_train=tf.stack([u1_train,u2_train,u3_train,u4_train],axis=1)
    v_train=tf.stack([v1_train,v2_train,v3_train,v4_train],axis=1)
    u_train=tf.cast(u_train, dtype=tf.float32)
    v_train=tf.cast(v_train, dtype=tf.float32)
    #print(u_train)
    #print(v_train)

#    model1=myModel()

#    model1.compile(optimizer='adam', loss='mse')

#checkpoint_save_path="./checkpoint/mnist.ckpt"
#if os.path.exists(checkpoint_save_path + '.index'):
#  print('-------------------load the model---------------------')
#  model1.load_weights(checkpoint_save_path)

#cp_callback=tf.keras.callbacks.ModelCheckpoint(filepath=checkpoint_save_path,
#                        save_weights_only=True,
#                        save_best_only=True)

#history=model1.fit(u_train, v_train, batch_size=128, epochs=1000, validation_split=0.01, validation_freq=20, callbacks=[cp_callback])

    model1.fit(u_train, v_train, batch_size=128, epochs=1000, validation_split=0.01, validation_freq=20, verbose=0)

#    model1.summary()

0 ---------------------------------------
0 2.7175397872924805
1 0.0616881288588047
2 2.053833246231079
3 0.030419671908020973
4 1.4932537078857422
5 0.02871217019855976
6 1.1771931648254395
7 0.023063698783516884
8 1.0697506666183472
9 0.026180552318692207
10 0.9103687405586243
11 0.019279034808278084
12 0.8395211696624756
13 0.02153976634144783
14 0.7419089674949646
15 0.03428361564874649
16 0.6869016289710999
17 0.04788533225655556
18 0.6743290424346924
19 0.05748472362756729
20 2.0937447547912598
21 0.04179300367832184
22 1.5610636472702026
23 0.03092912770807743
24 1.2140333652496338
25 0.02545519918203354
26 1.0142704248428345
27 0.023437680676579475
28 0.8875942826271057
29 0.020936673507094383
30 0.8011680245399475
31 0.026260392740368843
32 0.7382265329360962
33 0.03815903887152672
34 0.6722380518913269
35 0.0416746623814106
36 0.6080846786499023
37 0.05526776984333992
38 0.5909069180488586
39 0.09017572551965714
40 1.6559302806854248
41 0.04599245637655258
42 1.38577175140380

In [15]:
## 计算subsystem 2   keras resnet
L1=L
L1=np.delete(L,I)
I02=tf.argmax(L1)
print(I02)

i=2*I02
u1_train =xdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])]
u2_train =ydata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])]
u3_train =zdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])]
u4_train =wdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])]
v1_train =xdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)]
v2_train =ydata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)]
v3_train =zdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)]
v4_train =wdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)]
#x_train =tf.reduce_sum(xdata, axis=0)
#y_train =tf.reduce_sum(ydata, axis=0)
u_train=tf.stack([u1_train,u2_train,u3_train,u4_train],axis=1)
v_train=tf.stack([v1_train,v2_train,v3_train,v4_train],axis=1)
u_train=tf.cast(u_train, dtype=tf.float32)
v_train=tf.cast(v_train, dtype=tf.float32)
print(iptnp)
print(u_train)
print(v_train)

class myModel2(Model):
  def __init__(self):
    super(myModel2,self).__init__()
    self.layer1=Dense(20, activation='relu')
    self.layer2=Dense(20, activation='relu')
    self.layer3=Dense(20, activation='relu')
    self.layer4=Dense(20, activation='relu')
    self.layer5=Dense(20, activation='relu')
    self.layer6=Dense(20, activation='relu')
    self.layer7=Dense(20, activation='relu')
    self.layer8=Dense(20, activation='relu')
    self.layer9=Dense(4, kernel_regularizer=tf.keras.regularizers.l2())
  
  def call(self, x):
    x1=self.layer1(x)
    x1=self.layer2(x1)
    x1=self.layer3(x1)
    x1=self.layer4(x1)
    x1=self.layer5(x1)
    x1=self.layer6(x1)
    x1=self.layer7(x1)
    x1=self.layer8(x1)
    y=self.layer9(x1)
    y=y+x
    return y

model2=myModel2()

model2.compile(optimizer='adam', loss='mse')

model2.fit(u_train, v_train, batch_size=128, epochs=2000, validation_split=0.01, validation_freq=20)

model2.summary()



tf.Tensor(0, shape=(), dtype=int64)
[  0 209 798   0 184 798   0 162 798   0 146 798   0 141 798   0 132 798
   0 129 798   0 123 798   0 120 798   0 119 798   0 186 798   0 163 798
   0 147 798   0 139 798   0 131 798   0 126 798   0 122 798   0 119 798
   0 114 798   0 111 798   0 168 798   0 154 798   0 142 798   0 131 798
   0 121 798   0 116 798   0 112 798   0 109 798   0 110 798   0 104 798
   0 160 798   0 144 798   0 131 798   0 118 798   0 117 798   0 111 798
   0 105 798   0 100 798   0 100 798   0 100 798   0 153 798   0 140 798
   0 122 798   0 116 798   0 111 798   0 105 798   0 100 798   0 100 798
   0  94 798   0  93 798   0 141 798   0 128 798   0 116 798   0 109 798
   0 105 798   0  99 798   0  96 798   0  91 798   0  90 798   0  87 798
   0 137 798   0 122 798   0 115 798   0 103 798   0  96 798   0  91 798
   0  91 798   0  86 798   0  83 798   0  83 798   0 130 798   0 115 798
   0 105 798   0  97 798   0  94 798   0  87 798   0  86 798   0  80 798
   0  79 798   

In [16]:
## 计算其他几段数据误差
LI0=0
for k in range(10):
    print(k,'---------------------------------------')
    Llen=L.size
    error=np.zeros([Llen])
    for i in range(Llen):
        x1=tf.cast(xdata[LS*(i//Ls)+iptnp[i+i//Ls]], dtype=tf.float32)
        x1=tf.reshape(x1,[1])
        x2=tf.cast(ydata[LS*(i//Ls)+iptnp[i+i//Ls]],dtype=tf.float32)
        x2=tf.reshape(x2,[1])
        x3=tf.cast(zdata[LS*(i//Ls)+iptnp[i+i//Ls]],dtype=tf.float32)
        x3=tf.reshape(x3,[1])
        x4=tf.cast(wdata[LS*(i//Ls)+iptnp[i+i//Ls]],dtype=tf.float32)
        x4=tf.reshape(x4,[1])
        u=tf.stack([x1,x2,x3,x4],axis=1)
        y1=np.zeros([4,L[i]])
        u1=tf.reduce_sum(u,axis=0)
        y1[:,0]=u1.numpy()
        for j in range(L[i]-1):
            clear_session()
            v=model2.predict(u, verbose=0)
            v=tf.constant(v)
            u=v
            y1[:,j+1]=v.numpy()
        
        y1=tf.cast(y1, dtype=tf.float32)
        ytrue1=tf.cast(xdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])], dtype=tf.float32)
        ytrue2=tf.cast(ydata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])], dtype=tf.float32)
        ytrue3=tf.cast(zdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])], dtype=tf.float32)
        ytrue4=tf.cast(wdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])], dtype=tf.float32)
        ytrue=tf.stack([ytrue1,ytrue2,ytrue3,ytrue4],axis=0)
        y=(y1-ytrue).numpy()
        #print(i,y1,ytrue)
        error[i]=tf.reduce_mean(np.power(y[0,:],2)+np.power(y[1,:],2)+np.power(y[2,:],2)+np.power(y[3,:],2),axis=0)
        print(i,error[i])
    
    print(error)
    
    
    I2=np.where(error<1e-1)[0]
    LI=I2.size
    print(I2)
    if LI==LI0:
        break
    LI0=LI
    
    u1_train =np.zeros([0])
    u2_train =np.zeros([0])
    u3_train =np.zeros([0])
    u4_train =np.zeros([0])
    v1_train =np.zeros([0])
    v2_train =np.zeros([0])
    v3_train =np.zeros([0])
    v4_train =np.zeros([0])
    for i in I2:
        u1_train=np.append(u1_train, xdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])])
        u2_train=np.append(u2_train, ydata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])])
        u3_train=np.append(u3_train, zdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])])
        u4_train=np.append(u4_train, wdata[(LS*(i//Ls)+iptnp[i+i//Ls]):(LS*(i//Ls)+iptnp[i+1+i//Ls])])
        v1_train=np.append(v1_train, xdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)])
        v2_train=np.append(v2_train, ydata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)])
        v3_train=np.append(v3_train, zdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)])
        v4_train=np.append(v4_train, wdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+1+i//Ls]+1)])
    
    u_train=tf.stack([u1_train,u2_train,u3_train,u4_train],axis=1)
    v_train=tf.stack([v1_train,v2_train,v3_train,v4_train],axis=1)
    u_train=tf.cast(u_train, dtype=tf.float32)
    v_train=tf.cast(v_train, dtype=tf.float32)
    #print(u_train)
    #print(v_train)

#    model2=myModel2()

#    model2.compile(optimizer='adam', loss='mse')

#checkpoint_save_path="./checkpoint/mnist.ckpt"
#if os.path.exists(checkpoint_save_path + '.index'):
#  print('-------------------load the model---------------------')
#  model1.load_weights(checkpoint_save_path)

#cp_callback=tf.keras.callbacks.ModelCheckpoint(filepath=checkpoint_save_path,
#                        save_weights_only=True,
#                        save_best_only=True)

#history=model2.fit(u_train, v_train, batch_size=128, epochs=1000, validation_split=0.01, validation_freq=20, callbacks=[cp_callback])

    model2.fit(u_train, v_train, batch_size=128, epochs=1000, validation_split=0.01, validation_freq=20, verbose=0)

#    model2.summary()

0 ---------------------------------------
0 0.0006509168888442218
1 23.637258529663086
2 0.0018997224979102612
3 23.513418197631836
4 0.004875596147030592
5 23.456262588500977
6 0.010310962796211243
7 23.790939331054688
8 0.011755852960050106
9 24.004737854003906
10 0.017292167991399765
11 24.34946632385254
12 0.02013831026852131
13 24.608980178833008
14 0.029472067952156067
15 25.065587997436523
16 0.03408379480242729
17 25.4689998626709
18 0.04248938709497452
19 25.704893112182617
20 0.002159356838092208
21 24.023027420043945
22 0.006484703626483679
23 23.95376205444336
24 0.011748104356229305
25 24.149038314819336
26 0.015416569076478481
27 24.142972946166992
28 0.01794646680355072
29 24.574542999267578
30 0.022669760510325432
31 24.771324157714844
32 0.02840588055551052
33 25.2401065826416
34 0.03374236822128296
35 25.44377326965332
36 0.03888419270515442
37 25.996511459350586
38 0.05067799612879753
39 26.552188873291016
40 0.007625975646078587
41 24.658222198486328
42 0.0106012020

In [18]:
## Inferring Transition Logic
x11 =np.zeros([0])
x12 =np.zeros([0])
x13 =np.zeros([0])
x14 =np.zeros([0])
for i in I:
    x11=np.append(x11,xdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+i//Ls+1])])
    x12=np.append(x12,ydata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+i//Ls+1])])
    x13=np.append(x13,zdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+i//Ls+1])])
    x14=np.append(x14,zdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+i//Ls+1])])
    
L0=x11.shape[0]
J1=np.ones(L0)
J2=0*np.ones(L0)
x_train1=tf.stack([x11,x12,x13,x14,J1,J2],axis=1)

x31 =np.zeros([0])
x32 =np.zeros([0])
x33 =np.zeros([0])
x34 =np.zeros([0])
x41 =np.zeros([0])
x42 =np.zeros([0])
x43 =np.zeros([0])
x44 =np.zeros([0])
for i in I2:
    x31=np.append(x31,xdata[(LS*(i//Ls)+iptnp[i+i//Ls+1])])
    x32=np.append(x32,ydata[(LS*(i//Ls)+iptnp[i+i//Ls+1])])
    x33=np.append(x33,zdata[(LS*(i//Ls)+iptnp[i+i//Ls+1])])
    x34=np.append(x34,wdata[(LS*(i//Ls)+iptnp[i+i//Ls+1])])
    x41=np.append(x41,xdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+i//Ls+1])])
    x42=np.append(x42,ydata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+i//Ls+1])])
    x43=np.append(x43,zdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+i//Ls+1])])
    x44=np.append(x44,wdata[(LS*(i//Ls)+iptnp[i+i//Ls]+1):(LS*(i//Ls)+iptnp[i+i//Ls+1])])
    
L0=x31.shape[0]
J1=0*np.ones(L0)
J2=np.ones(L0)
x_train3=tf.stack([x31,x32,x33,x34,J1,J2],axis=1)
L0=x41.shape[0]
J1=0*np.ones(L0)
J2=np.ones(L0)
x_train4=tf.stack([x41,x42,x43,x44,J1,J2],axis=1)

x_train1=tf.cast(x_train1,dtype=tf.float32)
x_train3=tf.cast(x_train3,dtype=tf.float32)
x_train4=tf.cast(x_train4,dtype=tf.float32)
print(x_train1,x_train3,x_train4)
tf_optimizer = tf.keras.optimizers.Adam(learning_rate=0.002,beta_1=0.999,epsilon=1e-1)
#tf_optimizer = tf.keras.optimizers.Adam(learning_rate=0.1,beta_1=0.99,epsilon=1e-1)

class myModel_ITL():
  def __init__(self,optimizer,x_train1,x_train3,x_train4):
    self.u_model=tf.keras.Sequential()
    self.u_model.add(tf.keras.layers.InputLayer(input_shape=(6,)))
    self.u_model.add(tf.keras.layers.Dense(
      20, activation=tf.nn.relu,
      kernel_initializer='glorot_normal'))
    self.u_model.add(tf.keras.layers.Dense(
      20, activation=tf.nn.relu,
      kernel_initializer='glorot_normal'))
    self.u_model.add(tf.keras.layers.Dense(
      20, activation=tf.nn.relu,
      kernel_initializer='glorot_normal'))
    self.u_model.add(tf.keras.layers.Dense(
      20, activation=tf.nn.relu,
      kernel_initializer='glorot_normal'))
    self.u_model.add(tf.keras.layers.Dense(
      20, activation=tf.nn.relu,
      kernel_initializer='glorot_normal'))
    self.u_model.add(tf.keras.layers.Dense(
      20, activation=tf.nn.relu,
      kernel_initializer='glorot_normal'))
    self.u_model.add(tf.keras.layers.Dense(
      20, activation=tf.nn.relu,
      kernel_initializer='glorot_normal'))
    self.u_model.add(tf.keras.layers.Dense(
      20, activation=tf.nn.relu,
      kernel_initializer='glorot_normal'))
    self.u_model.add(tf.keras.layers.Dense(
      2, activation=tf.nn.softmax,
      kernel_initializer='glorot_normal'))
        
    self.optimizer=optimizer
    self.dtype=tf.float32

  # Defining custom loss
  def __loss(self):
    y1NN=self.u_model(x_train1)
    y1=y1NN[:,0]
    y3NN=self.u_model(x_train3)
    y3=y3NN[:,0]
    y4NN=self.u_model(x_train4)
    y4=y4NN[:,1]
    return tf.reduce_mean(-tf.math.log(y1),axis=0)  + \
     tf.reduce_mean(-tf.math.log(y3),axis=0)  + \
     tf.reduce_mean(-tf.math.log(y4),axis=0)

  def __grad(self):
    with tf.GradientTape() as tape:
      loss_value = self.__loss()
    return loss_value, tape.gradient(loss_value, self.__wrap_training_variables())
    
  def __wrap_training_variables(self):
    var = self.u_model.trainable_variables
    return var
    
  def summary(self):
    return self.u_model.summary()

  # The training function
  def fit(self, tf_epochs=5000):
    # Creating the tensors
    #X_u = tf.convert_to_tensor(X_u, dtype=self.dtype)
    #u = tf.convert_to_tensor(u, dtype=self.dtype)
    #print(self.__wrap_training_variables())

    LOSS=np.zeros([1,tf_epochs])
    for epoch in range(tf_epochs):
      # Optimization step
      loss_value, grads = self.__grad()
      self.optimizer.apply_gradients(zip(grads, self.__wrap_training_variables()))
      LOSS[0,epoch]=loss_value.numpy()
      print('epoch, loss_value:', epoch, loss_value)

    scio.savemat('LOSS.mat',{'LOSS':LOSS})
    
  def predict(self, X_star):
    u_star = self.u_model(X_star)
    return u_star

    
model_ITL=myModel_ITL(tf_optimizer, x_train1, x_train3, x_train4)

model_ITL.fit(tf_epochs=100000)

model_ITL.summary()


tf.Tensor(
[[0.40646118 2.5545464  0.25871718 0.25871718 1.         0.        ]
 [0.40920213 2.5465503  0.25741506 0.25741506 1.         0.        ]
 [0.41309372 2.5388167  0.25704145 0.25704145 1.         0.        ]
 ...
 [3.4799976  0.5179747  0.9027009  0.9027009  1.         0.        ]
 [3.481605   0.517278   0.9012253  0.9012253  1.         0.        ]
 [3.4832873  0.51680887 0.9004552  0.9004552  1.         0.        ]], shape=(68510, 6), dtype=float32) tf.Tensor(
[[ 0.40246433  2.5617733   0.25991738 10.45        0.          1.        ]
 [ 0.3997049   2.269783    0.36285594  9.2         0.          1.        ]
 [ 0.40037408  1.986406    0.4944399   8.1         0.          1.        ]
 [ 0.40015295  1.7959089   0.58249164  7.3         0.          1.        ]
 [ 0.40302736  1.7202162   0.68261474  7.05        0.          1.        ]
 [ 0.39995605  1.6156415   0.80536085  6.6         0.          1.        ]
 [ 0.4004452   1.5590366   0.9002068   6.45        0.          1.        ]

In [23]:
## validation
x1=tf.constant([0], dtype=tf.float32)
x2=tf.constant([0.5], dtype=tf.float32)
x3=tf.constant([0.6283], dtype=tf.float32)
x4=tf.constant([0], dtype=tf.float32)
x5=tf.constant([0], dtype=tf.float32)
x6=tf.constant([1], dtype=tf.float32)
NT=799
X=x1
Y=x2
Z=x3
W=x4
for i in range(NT):
    x=tf.stack([x1,x2,x3,x4],axis=1)
    if x5>0.5:
        y=model1.predict(x, verbose=0)
    else:
        y=model2.predict(x, verbose=0)
    x_t=tf.stack([x1,x2,x3,x4,x5,x6],axis=1)
    y_t=model_ITL.predict(x_t)
    
    X=np.append(X,y[0,0])
    Y=np.append(Y,y[0,1])
    Z=np.append(Z,y[0,2])
    W=np.append(W,y[0,3])
    x1=y[0,0]
    x1=tf.reshape(x1,[1])
    x2=y[0,1]
    x2=tf.reshape(x2,[1])
    x3=y[0,2]
    x3=tf.reshape(x3,[1])
    x4=y[0,3]
    x4=tf.reshape(x4,[1])
    print(i,y,y_t,x5,x6)
    if y_t[0,0]>0.5:
        x5=tf.constant([1], dtype=tf.float32)
        x6=tf.constant([0], dtype=tf.float32)
    else:
        x5=tf.constant([0], dtype=tf.float32)
        x6=tf.constant([1], dtype=tf.float32)

scio.savemat('validationx.mat',{'X':X})
scio.savemat('validationy.mat',{'Y':Y})
scio.savemat('validationz.mat',{'Z':Z})
scio.savemat('validationw.mat',{'W':W})
print(X,Y,Z,W)

0 [[0.00134317 0.500046   0.62657595 0.05000047]] tf.Tensor([[3.6017996e-14 1.0000000e+00]], shape=(1, 2), dtype=float32) tf.Tensor([0.], shape=(1,), dtype=float32) tf.Tensor([1.], shape=(1,), dtype=float32)
1 [[0.00266419 0.5003817  0.6248167  0.10000095]] tf.Tensor([[3.563261e-14 1.000000e+00]], shape=(1, 2), dtype=float32) tf.Tensor([0.], shape=(1,), dtype=float32) tf.Tensor([1.], shape=(1,), dtype=float32)
2 [[0.00398042 0.50103664 0.62304026 0.15000142]] tf.Tensor([[3.5254172e-14 1.0000000e+00]], shape=(1, 2), dtype=float32) tf.Tensor([0.], shape=(1,), dtype=float32) tf.Tensor([1.], shape=(1,), dtype=float32)
3 [[0.00530433 0.5020365  0.6212603  0.2000019 ]] tf.Tensor([[3.4807182e-14 1.0000000e+00]], shape=(1, 2), dtype=float32) tf.Tensor([0.], shape=(1,), dtype=float32) tf.Tensor([1.], shape=(1,), dtype=float32)
4 [[0.0066368  0.50338095 0.61947787 0.25000235]] tf.Tensor([[3.4372675e-14 1.0000000e+00]], shape=(1, 2), dtype=float32) tf.Tensor([0.], shape=(1,), dtype=float32) tf.Te